<a href="https://colab.research.google.com/github/BharathiVetukuri/CMPE-255_DataMining_Autogluon/blob/main/Text_Semantic_Search.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install autogluon.multimodal
!pip install ir_datasets
!pip install rank_bm25

  Using cached torch-2.3.1-cp310-cp310-manylinux1_x86_64.whl.metadata (26 kB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached triton-2.3.1-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (1.4 kB)
Using cached torch-2.3.1-cp310-cp310-manylinux1_x86_64.whl (779.1 MB)
Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
Using cached triton-2.3.1-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (168.1 MB)
  Attempting uninstall: triton
    Found existing installation: triton 3.0.0
    Uninstalling triton-3.0.0:
      Successfully uninstalled triton-3.0.0
  Attempting uninstall: nvidia-cudnn-cu12
    Found existing installation: nvidia-cudnn-cu12 9.1.0.70
    Uninstalling nvidia-cudnn-cu12-9.1.0.70:
      Successfully uninstalled nvidia-cudnn-cu12-9.1.0.70
  Attempting uninstall: torch
    Found existing installation: torch 2.4.1
    Uninstalling torch-2.4.1:
      Successful

In [ ]:
!pip uninstall -y torch torchvision torchaudio autogluon
!pip install torch==2.0.1 torchvision==0.15.2 torchaudio==2.0.2
!pip install autogluon==0.6.0
!pip install ir_datasets
!pip install rank_bm25

Found existing installation: torch 2.3.1
Uninstalling torch-2.3.1:
  Successfully uninstalled torch-2.3.1
Found existing installation: torchvision 0.18.1
Uninstalling torchvision-0.18.1:
  Successfully uninstalled torchvision-0.18.1
Found existing installation: torchaudio 2.4.1+cu121
Uninstalling torchaudio-2.4.1+cu121:
  Successfully uninstalled torchaudio-2.4.1+cu121
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 619.9/619.9 MB 2.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.0/6.0 MB 56.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.4/4.4 MB 52.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 317.1/317.1 MB 4.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.8/11.8 MB 69.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.0/21.0 MB 50.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 849.3/849.3 kB 32.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 557.1/557.1 MB 2.9 MB/s eta 0:0

In [ ]:
import ir_datasets
import pandas as pd
from collections import defaultdict
import string
import nltk
import numpy as np
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from rank_bm25 import BM25Okapi
from autogluon.multimodal import MultiModalPredictor
from autogluon.multimodal.utils import compute_ranking_score, semantic_search


In [ ]:
nltk.download('stopwords')
nltk.download('punkt')

# Load dataset
dataset = ir_datasets.load("beir/nfcorpus/test")

# Prepare dataframes
doc_data = pd.DataFrame(dataset.docs_iter())
query_data = pd.DataFrame(dataset.queries_iter())
labeled_data = pd.DataFrame(dataset.qrels_iter())

# Clean up the data
query_data = query_data.drop("url", axis=1)
doc_data['text'] = doc_data[['text', 'title']].apply(" ".join, axis=1)
doc_data = doc_data.drop(["title", "url"], axis=1)


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[INFO] [starting] building docstore
[INFO] [starting] opening zip file
[INFO] [starting] https://public.ukp.informatik.tu-darmstadt.de/thakur/BEIR/datasets/nfcorpus.zip
docs_iter:   0%|                                      | 0/3633 [00:00<?, ?doc/s]
https://public.ukp.informatik.tu-darmstadt.de/thakur/BEIR/datasets/nfcorpus.zip: 0.0%| 0.00/2.45M [00:00<?, ?B/s]
https://public.ukp.informatik.tu-darmstadt.de/thakur/BEIR/datasets/nfcorpus.zip: 0.7%| 16.4k/2.45M [00:00<00:27, 89.5kB/s]
https://public.ukp.informatik.tu-darmstadt.de/thakur/BEIR/datasets/nfcorpus.zip: 2.0%| 49.2k/2.45M [00:00<00:23, 102kB/s] 
https://public.ukp.informatik.tu-darmstadt.de/thakur/BEIR/datasets/nfcorpus.zip: 3.3%| 81.9k/2.45M [00:00<00:19, 121kB/s]
https://public.ukp.informatik.tu-darmstadt.de/thaku

In [ ]:
def get_qrels(dataset):
    qrel_dict = defaultdict(dict)
    for qrel in dataset.qrels_iter():
        qrel_dict[qrel.query_id][qrel.doc_id] = qrel.relevance
    return qrel_dict

def compute_ndcg(results, qrel_dict, cutoffs):
    return compute_ranking_score(results=results, qrel_dict=qrel_dict, metrics=["ndcg"], cutoffs=cutoffs)

qrel_dict = get_qrels(dataset)


In [ ]:
def tokenize_corpus(corpus):
    stop_words = set(stopwords.words("english") + list(string.punctuation))
    tokenized_docs = []
    for doc in corpus:
        tokens = nltk.word_tokenize(doc.lower())
        tokenized_doc = [w for w in tokens if w not in stop_words and len(w) > 2]
        tokenized_docs.append(tokenized_doc)
    return tokenized_docs

def rank_documents_bm25(queries_text, queries_id, docs_id, top_k, bm25):
    tokenized_queries = tokenize_corpus(queries_text)
    results = {qid: {} for qid in queries_id}
    for query_idx, query in enumerate(tokenized_queries):
        scores = bm25.get_scores(query)
        scores_top_k_idx = np.argsort(scores)[::-1][:top_k]
        for doc_idx in scores_top_k_idx:
            results[queries_id[query_idx]][docs_id[doc_idx]] = float(scores[doc_idx])
    return results

def evaluate_bm25(doc_data, query_data, qrel_dict, cutoffs):
    tokenized_corpus = tokenize_corpus(doc_data['text'].tolist())
    bm25_model = BM25Okapi(tokenized_corpus, k1=1.2, b=0.75)

    results = rank_documents_bm25(query_data['text'].tolist(), query_data['query_id'].tolist(), doc_data['doc_id'].tolist(), max(cutoffs), bm25_model)
    return compute_ndcg(results, qrel_dict, cutoffs)

cutoffs = [5, 10, 20]
evaluate_bm25(doc_data, query_data, qrel_dict, cutoffs)


{'ndcg@5': 0.33858, 'ndcg@10': 0.29827, 'ndcg@20': 0.26384}

In [ ]:
predictor = MultiModalPredictor(
    query='query_id',
    response='doc_id',
    label='relevance',
    problem_type='text_similarity',
    hyperparameters={"model.hf_text.checkpoint_name": "sentence-transformers/all-MiniLM-L6-v2"}
)

predictor.evaluate(
    labeled_data,
    query_data=query_data[['query_id']],
    response_data=doc_data[['doc_id']],
    id_mappings={ 'query_id': query_data.set_index('query_id')['text'], 'doc_id': doc_data.set_index('doc_id')['text'] },
    cutoffs=cutoffs,
    metrics=['ndcg'],
)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1150: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/612 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/90.9M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/350 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

...

/usr/local/lib/python3.10/dist-packages/numpy/core/fromnumeric.py:59: FutureWarning: 'DataFrame.swapaxes' is deprecated and will be removed in a future version. Please use 'DataFrame.transpose' instead.
  return bound(*args, **kwds)


Predicting: |          | 0/? [00:00<?, ?it/s]

Predicting: |          | 0/? [00:00<?, ?it/s]

Predicting: |          | 0/? [00:00<?, ?it/s]

{'ndcg@5': 0.34429, 'ndcg@10': 0.31019, 'ndcg@20': 0.28686}

In [ ]:
hits = semantic_search(
    matcher=predictor,
    query_data=query_data['text'].tolist(),
    response_data=doc_data['text'].tolist(),
    query_chunk_size=len(query_data),
    top_k=max(cutoffs),
)


Predicting: |          | 0/? [00:00<?, ?it/s]

Predicting: |          | 0/? [00:00<?, ?it/s]

In [ ]:
query_embeds = predictor.extract_embedding(query_data[['query_id']], id_mappings={ 'query_id': query_data.set_index('query_id')['text'] }, as_tensor=True)
doc_embeds = predictor.extract_embedding(doc_data[['doc_id']], id_mappings={ 'doc_id': doc_data.set_index('doc_id')['text'] }, as_tensor=True)


Predicting: |          | 0/? [00:00<?, ?it/s]

Predicting: |          | 0/? [00:00<?, ?it/s]

In [ ]:
!pip install torch

In [ ]:
import torch
from rank_bm25 import BM25Okapi

In [ ]:
query_id_col = "query_id"  # Define globally
doc_id_col = "doc_id"      # Define globally
text_col = "text"          # Define globally

def hybridBM25(query_data, query_embeds, doc_data, doc_embeds, recall_num, top_k, beta):
    global text_col  # Access the global variable
    # Recall documents with BM25 scores
    tokenized_corpus = tokenize_corpus(doc_data[text_col].tolist())
    bm25_model = BM25Okapi(tokenized_corpus, k1=1.2, b=0.75)
    bm25_scores = rank_documents_bm25(query_data[text_col].tolist(), query_data[query_id_col].tolist(), doc_data[doc_id_col].tolist(), recall_num, bm25_model)

    # Continue with the rest of the function...

    # Debugging print statements
    print(f"BM25 Scores: {bm25_scores}")

    all_bm25_scores = [score for scores in bm25_scores.values() for score in scores.values()]
    max_bm25_score = max(all_bm25_scores)
    min_bm25_score = min(all_bm25_scores)

    q_embeddings = {qid: embed for qid, embed in zip(query_data[query_id_col].tolist(), query_embeds)}
    d_embeddings = {did: embed for did, embed in zip(doc_data[doc_id_col].tolist(), doc_embeds)}

    query_ids = query_data[query_id_col].tolist()
    results = {qid: {} for qid in query_ids}
    for idx, qid in enumerate(query_ids):
        rec_docs = bm25_scores[qid]
        rec_doc_emb = [d_embeddings[doc_id] for doc_id in rec_docs.keys()]
        rec_doc_id = [doc_id for doc_id in rec_docs.keys()]

        # Check if there are retrieved documents
        if not rec_docs:
            print(f"No documents retrieved for query ID: {qid}")
            continue

        rec_doc_emb = torch.stack(rec_doc_emb)
        scores = compute_semantic_similarity(q_embeddings[qid], rec_doc_emb)
        scores[torch.isnan(scores)] = -1

        top_k_values, top_k_idxs = torch.topk(
            scores,
            min(top_k + 1, len(scores[0])),
            dim=1,
            largest=True,
            sorted=False,
        )

        for doc_idx, score in zip(top_k_idxs[0], top_k_values[0]):
            doc_id = rec_doc_id[int(doc_idx)]
            # Hybrid scores from BM25 and cosine similarity of embeddings
            results[qid][doc_id] = \
                (1 - beta) * float(score.numpy()) \
                + beta * (bm25_scores[qid][doc_id] - min_bm25_score) / (max_bm25_score - min_bm25_score)

    # Debugging: Check results before return
    print(f"Results: {results}")

    return results


In [ ]:
print(f"Query Data: {query_data.head()}")
print(f"Query Embeds Shape: {query_embeds.shape if query_embeds is not None else 'None'}")
print(f"Document Data: {doc_data.head()}")
print(f"Document Embeds Shape: {doc_embeds.shape if doc_embeds is not None else 'None'}")


Query Data:    query_id                                               text
0   PLAIN-2   Do Cholesterol Statin Drugs Cause Breast Cancer?
1  PLAIN-12                Exploiting Autophagy to Live Longer
2  PLAIN-23  How to Reduce Exposure to Alkylphenols Through...
3  PLAIN-33          What’s Driving America’s Obesity Problem?
4  PLAIN-44              Who Should be Careful About Curcumin?
Query Embeds Shape: torch.Size([323, 384])
Document Data:     doc_id                                               text
0   MED-10  Recent studies have suggested that statins, an...
1   MED-14  BACKGROUND: Preclinical studies have shown tha...
2  MED-118  The aims of this study were to determine the c...
3  MED-301  Epilepsy or seizure disorder is one of the mos...
4  MED-306  Hit Reaction Time latencies (HRT) in the Conti...
Document Embeds Shape: torch.Size([3633, 384])


In [ ]:
evaluate_hybridBM25(query_data, query_embeds, doc_data, doc_embeds, recall_num, beta, cutoffs)


BM25 Scores: {'PLAIN-2': {'MED-10': 17.740870713871228, 'MED-2429': 17.017503431917515, 'MED-14': 16.702994146856415, 'MED-2431': 16.037629072292408, 'MED-4827': 15.768139869669923, 'MED-1193': 15.568955292508287, 'MED-2427': 12.921860931623307, 'MED-4829': 12.681274951514105, 'MED-4650': 11.650473660239344, 'MED-4562': 11.494037796805218, 'MED-2434': 11.165484468939452, 'MED-3830': 10.581820939679915, 'MED-3834': 10.581820939679915, 'MED-2439': 10.551715605891923, 'MED-3551': 10.410230296821036, 'MED-958': 10.239006749806814, 'MED-1887': 10.051923070289895, 'MED-4450': 10.032982846588972, 'MED-2435': 9.783827302735903, 'MED-1207': 9.532836792852896, 'MED-3843': 9.449035610402909, 'MED-3110': 9.446421240954784, 'MED-2107': 9.390041488039401, 'MED-3550': 9.236936714208184, 'MED-3726': 9.232776077930655, 'MED-2440': 9.213048751582146, 'MED-4830': 9.199875430098045, 'MED-4695': 9.187832764228641, 'MED-3795': 9.120237258266433, 'MED-2428': 9.096203433813201, 'MED-5066': 9.027681626361828, 

NameError: name 'compute_semantic_similarity' is not defined